In [374]:
#+++ версия 2022.05.10 инициализация посредством global init()
from importlib import reload
import sys; 
sys.path.append("../../lib/")

# pd.set_option('mode.chained_assignment', None)

from  colorise import * 
from  geo import * 

import adds
adds = reload(adds)
from adds import * # import adds functions

init()


pd.set_option('mode.chained_assignment',None)

ii(dfr,1)

0:00:00.000 ₀╷₀₀╷₀₀.₀₀₀ init()


In [3]:
sys.path.append("../../settings/")

if 'creds' in sys.modules.keys(): del sys.modules['creds'];
import  creds
# print(creds.pg_creds)

In [371]:
del sys.modules['colorise'];
from  colorise import * 
# colorise_palettes()

In [ ]:
amazfit = '''<trkpt lat="55.689453" lon="37.353127">
                <time>2022-05-10T05:22:51Z</time>
                <desc><![CDATA[CommonTimeValuePoint(absoluteTime=1652160171, value=1.8)]]></desc>
                    <extensions>
                        <ns3:TrackPointExtension>
                            <ns3:speed>0.0</ns3:speed>
                        </ns3:TrackPointExtension>
                    </extensions>
            </trkpt>'''

strava =  '''<trkpt lat="55.7154400" lon="37.3633300">
                <ele>105.2</ele>
                <time>2022-05-02T12:03:21Z</time>
                <extensions>
                 <gpxtpx:TrackPointExtension>
                  <gpxtpx:atemp>22</gpxtpx:atemp>
                 </gpxtpx:TrackPointExtension>
                </extensions>
              </trkpt>'''

In [419]:
ii(dfr)

In [421]:
#@@ 2022-05-10 count elevation 
tm()

print (dfr['Zepp20220510114943_GPS strange'].shape[0])

df =dfr['Zepp20220510114943_GPS strange'][:1]

def get_elevation(df):
    elev =[]
    chunk_size = 100
    dfshape0 = df.shape[0]
    for chunk in range(0, dfshape0, chunk_size):
#         tm(chunk)

        d = df[chunk:chunk+chunk_size ]
        elev_points = "|".join((d['lat'].astype(str) + ',' + d['lon'].astype(str)))
        jsonurl = 'https://api.opentopodata.org/v1/srtm90m?locations=%s&interpolation=bilinear'%elev_points # nearest, bilinear, cubic. Default: bilinear.
        r = requests.get(jsonurl).json()
    #     print (elev_points, sonurl)
    #     print(r)
        if ('results' in r.keys()):
            for rr in r['results']:
                elev = elev + [rr['elevation']]
        else:
            time.sleep(1)
            delayed = get_elevation(d)
#             print (len(delayed))
            elev = elev + delayed
        print(dfshape0-chunk, end=',')             
    return elev

elev = get_elevation(df)            

df['ele'] = pd.DataFrame(elev)            
tm(['>>>',df.count()])


*** Start at: 22:20:41 ₂₀₂₂₋₀₅₋₁₀  ************************************************************
2672
1,0:00:00.257 ₀╷₀₀╷₀₀.₂₅₇ ['>>>', lon         1
lat         1
datetime    1
unixtime    1
ele         1
speed       1
dtype: int64]


1652210441.3462539

In [430]:
#  2022-05-10 Добавление высоты, сохранение обработанных треков в файл 

import xml.etree.ElementTree as ET
from datetime import datetime
import requests
import time
import json

tm()

dfr = {}

def parse_gpx(f):

    tree = ET.parse(f)

    prefix_map = {
        "n0": "http://www.topografix.com/GPX/1/1",
        "n1": "http://www.garmin.com/xmlschemas/TrackPointExtension/v1"
    }

    pnts = []

    for e in tree.findall("n0:trk/n0:trkseg/n0:trkpt", prefix_map)[::1]:
        p = {}
        p['lon'] = float(e.attrib['lon'])
        p['lat'] = float(e.attrib['lat'])
#         p['unixtime'] = int(e.findall("n0:desc", prefix_map)[0].text[34:44])
      
        p['datetime'] =  e.findall("n0:time", prefix_map)[0].text
        p['unixtime'] =  datetime.strptime(p['datetime'], "%Y-%m-%dT%H:%M:%SZ").timestamp()
        
        ele = e.findall("n0:ele", prefix_map)
        p['ele'] = float(ele[0].text) if len(ele) > 0 else -100
        
        speed = e.findall("n0:extensions/n1:TrackPointExtension/n1:speed", prefix_map)
        p['speed'] = speed[0].text if len(speed) > 0 else '-'
        
        pnts = pnts + [p] 
    
    dfp = pd.DataFrame(pnts) 
    
    elev = get_elevation(dfp)
    
    dfp['ele'] = pd.DataFrame(elev) 
    
    return dfp

f = gpx_files[6]



import glob
gpx_files = [f for f in glob.glob("data\\*.gpx")]
[[i,f] for i,f in enumerate(gpx_files)]

print (gpx_files)

for i,fl in enumerate(gpx_files[:]):
    df = parse_gpx(fl)   
    fname_parts = re.split('\.|\\\\',fl)
    fname = fname_parts[0]+'\pcl\\'+fname_parts[1]+".pcl"
    df.to_pickle(fname)
    tm(['\n',df.count(),fname_parts, fname])
    dfr[fname_parts[1]] = df
ii(dfr,1)    
tm('>>>')

*** Start at: 22:30:38 ₂₀₂₂₋₀₅₋₁₀  ************************************************************
['data\\7118301341.gpx', 'data\\Zepp20220508064546.gpx', 'data\\Zepp20220508174510.gpx', 'data\\Zepp20220508211224.gpx', 'data\\Zepp20220508211612.gpx', 'data\\Zepp20220509000808.gpx', 'data\\Zepp20220510114943_GPS strange.gpx']
1202,1102,1002,902,802,702,602,100,502,402,302,202,100,102,2,0:00:10.926 ₀╷₀₀╷₁₀.₉₂₆ ['\n', lon         1202
lat         1202
datetime    1202
unixtime    1202
ele         1202
speed       1202
dtype: int64, ['data', '7118301341', 'gpx'], 'data\\pcl\\7118301341.pcl']
100,1304,1204,1104,1004,100,904,804,704,604,100,504,404,304,204,100,104,4,0:00:14.297 ₀╷₀₀╷₂₅.₂₂₄ ['\n', lon         1304
lat         1304
datetime    1304
unixtime    1304
ele         1304
speed       1304
dtype: int64, ['data', 'Zepp20220508064546', 'gpx'], 'data\\pcl\\Zepp20220508064546.pcl']
3075,2975,100,2875,2775,2675,2575,100,2475,2375,2275,2175,100,2075,1975,1875,1775,100,1675,1575,1475,1375,100,

0:00:00.027 ₀╷₀₂╷₃₃.₄₂₂ >>>


1652211191.9112413

In [386]:
# 2022-05-10 add elevetion by lat lon to df

def add_max_min_elevation(m,df):
    
    ele_max = df['ele'].max()
    idmax = df['ele'].idxmax() 
    ele_max_ll = list(df.loc[idmax,['lat','lon']])
    

    
    ele_min = df['ele'].min()
    idmax = df['ele'].idxmin() 
    ele_min_ll = list(df.loc[idmax,['lat','lon']])
    
    
    mapMarker =  folium.Marker(location=ele_max_ll,
                      # Set icon to DivIcon to with conditional style formatting to reference the random temp value.
                      icon=folium.DivIcon(html=f"""<div style="width:20px; 
                                                  font-size:9px; 
                                                  color:#ffffff;
                                                  margin:-7px 0 0 -5px;
                                                  line-height: 1.5;
                                                  padding:2px 2px;
                                                  text-align:center;   
                                                  border-radius: 14px;
                                                  border: 1px solid #ffffff; 
                                                  background-color:#dd0000bb;">%.0f</div>"""% 
                                          (ele_max) 
                                         )
                     ).add_to(m)

    
    
    mapMarker =  folium.Marker(location=ele_min_ll,
                      # Set icon to DivIcon to with conditional style formatting to reference the random temp value.
                      icon=folium.DivIcon(html=f"""<div style="width:20px; 
                                                  font-size:9px; 
                                                  color:#ffffff;
                                                  margin:-7px 0 0 -5px;
                                                  line-height: 1.5;
                                                  padding:2px 2px;
                                                  text-align:center;   
                                                  border-radius: 14px;
                                                  border: 1px solid #ffffff; 
                                                  background-color:#0022ffbb;">%.0f</div>"""% 
                                          (ele_min) 
                                         )
                     ).add_to(m)   
ii(dfr,1)
add_max_min_elevation(gmap,dfr['7118301341'])    
# gmap

In [410]:
def add_marker(m,p,text):
        mapMarker =  folium.Marker(location=p,
                      # Set icon to DivIcon to with conditional style formatting to reference the random temp value.
                      icon=folium.DivIcon(html=f"""<div style="width:20px; 
                                                  font-size:9px; 
                                                  color:#ffffff;
                                                  margin:-7px 0 0 -5px;
                                                  line-height: 1.0;
                                                  padding:1px 1px;
                                                  text-align:center;   
                                                  border-radius: 2px;
                                                  border: 1px solid #ffffff; 
                                                  background-color:#888888bb;">%.0f</div>"""% 
                                          (text) 
                                         )
                     ).add_to(m)  

In [394]:
abs(-1)

1

In [429]:
# 2022-05-05 add elevation delet = 5 м, try point sample for next time для точности
import folium
from datetime import datetime
from datetime import timedelta
import matplotlib
tm()

global gmap
    
gmap = ""    

def draw_track_on_map(df, p=()):
    global gmap
    
    marker_colors = [c for c in sns.hls_palette(20, l=0.4, s=0.9).as_hex()]
    

    marker_colors = [matplotlib.colors.to_hex(c, keep_alpha=True) for c in sns.diverging_palette(150,10, s=120, l = 45, center="dark",sep=3, n=20)]
    
    
#     marker_colors = [matplotlib.colors.to_hex(sns.color_palette("icefire", as_cmap=True)(i/20), keep_alpha=True)  for i in range(0,20) ]
    
    [max_lat, max_lon] = df[['lat','lon']].max() 
    [min_lat, min_lon] = df[['lat','lon']].min() 
    
    
    marker_time  = start_time = df['unixtime'].min()
    total_points = df.shape[0]

    
    lat_start = df['lat'][0]
    lon_start = df['lon'][0]
    
    

    ele_max = df['ele'].max()
    ele_min = df['ele'].min()
    
    ele_prev = df['ele'][0]
    
    
    ele_delt = ele_max - ele_min
    
    print(ele_max, ele_min)
    
    
    dist = 0
    
    map_area = [
        [max_lat, max_lon],
        [max_lat, min_lon],
        [min_lat, min_lon],
        [min_lat, max_lon],
        [max_lat, max_lon]
           ]

    center = [(max_lat+min_lat)/2, (max_lon+min_lon)/2]
    
    f = folium.Figure(width=1600, height=800)
    
    

    tiles='https://api.mapbox.com/v4/mapbox.streets/{z}/{x}/{y}.png?access_token=mytoken'
    tiles='http://gpxlab.ru/strava.php?z={z}&x={x}&y={y}'
    


    if (gmap != ""):
        m = gmap
    else: 
        gmap = m = folium.Map(location=center, 
                   max_bounds=True,
#                    tiles=tiles,
#                    attr='Mapbox attribution'
                  ).add_to(f) 
    
    
    
    
    m.fit_bounds([map_area[0],map_area[2]])

    bounds=folium.PolyLine(locations=map_area ,weight=2,color='#ff880077')
    m.add_child(bounds)    
    m.add_child(folium.LatLngPopup())
        

    dist = 0    
    marker_dist = 0        
        
    
    for i,r in df.iterrows():
        lat = r['lat']
        lon = r['lon']
#         lat = r['lat_rolling_7']
#         lon = r['lon_rolling_7']        
        if (i>0):
            
            c = [[lat,lon], [next_lat, next_lon]]
            lap_dist = ll_distance(lat, lon, next_lat, next_lon)
            
            dist += lap_dist
            
            if (r['unixtime']-next_unixtime) == 0:
                counted_speed = 0
            else: 
                counted_speed = "%.1f"% (lap_dist/(r['unixtime']-next_unixtime)*3600)

            color = '#'+colorise(counted_speed, scooter_speed )+"55"
            
            if (r['ele'] < 0) | (abs(ele_prev - r['ele']) < 5):   #  elevetion delta 5 м
                w_height = 4 
            else:  
                w_height = 4+(r['ele'] - ele_min)*80/ele_max
                add_marker(m,list(r[['lat','lon']]),r['ele'])
                ele_prev = r['ele']
            
            
            tipText = '''<div>[%s]<b>%s</b></br>
                      s_device: %s</br>
                      s_counted: %s</br>
                      dist: %s</br>
                      elevation:%s [%0.0f,%0.0f]</div>'''%(i,r['datetime'],
                                      r['speed'],
                                      counted_speed,
                                      "%.1f"%(lap_dist*1000), 
                                      r['ele'],
                                      r['ele'] - ele_min,        
                                      ele_max - r['ele'],        
                     )
            
            my_PolyLine=folium.PolyLine(locations=c,
                                        weight=w_height,
                                        color=color,
                                        popup=tipText,
                                        tooltip=tipText
                                       )
            m.add_child(my_PolyLine)    
            
            
#             if(i%100 == 0):
#             if(r['unixtime'] - marker_time  >= 60):
            if(dist  >= marker_dist):

                marker_dist += 1
                marker_time += 60
                
                
                ll_next = ll_distance(lat_start, lon_start, next_lat, next_lon )
                ll = ll_distance(lat_start,lon_start, lat, lon )
                
                
                marker_color = "#33a02cff" if (ll > ll_next) else "#e31a1cff"
                
                
                marker_color = marker_colors[int(i / (total_points/20))]
                
                mapMarker =  folium.Marker(location=[lat, lon],
                      popup=tipText,
                      tooltip=tipText,
                      icon=folium.DivIcon(html=f"""<div style="width:40px; 
                                                  font-size:9px; 
                                                  color:%s;
                                                  margin:-7px 0 0 -15px;
                                                  line-height: 1.1;
                                                  padding:1px 2px;
                                                  text-align:center;   
                                                  border-radius: 7px;
                                                  border: 0px solid %s; 
                                                  background-color:#ffffffbb;">%s<br>%.2f</div>"""% 
                                          (marker_color, marker_color, timedelta(0, r['unixtime'] - start_time), dist) 
                                         )
                     ).add_to(m)
            
        next_lat = lat
        next_lon = lon
        next_unixtime = r['unixtime']
        
    add_max_min_elevation(m,df)
#     display(m)

params = (1000, 55.753145, 37.615845 , 0.3 , 1)

scooter_speed ={'#bb2202':3,
     '#FE0100':6,
     '#FEA000':9,
     '#FED000':12,
     '#FBFF00':15,
     '#03FF00':20,
     '#00B47B':25,
     '#04BBD9':30,
     '#358AFF':35,
     '#DC01dE':40,
     '#999999':10000
    }

import glob
gpx_pcl_files = [f for f in glob.glob("data\\pcl\\*")]
[[i,f] for i,f in enumerate(gpx_pcl_files)]
print (gpx_pcl_files)

for f in  gpx_pcl_files[6:]:
    df = pd.read_pickle(f)
    draw_track_on_map(df) # df[450:1500].reset_index()
    tm(f)
display(gmap)    

*** Start at: 22:28:10 ₂₀₂₂₋₀₅₋₁₀  ************************************************************
['data\\pcl\\7118301341.pcl', 'data\\pcl\\Zepp20220508064546.pcl', 'data\\pcl\\Zepp20220508174510.pcl', 'data\\pcl\\Zepp20220508211224.pcl', 'data\\pcl\\Zepp20220508211612.pcl', 'data\\pcl\\Zepp20220509000808.pcl', 'data\\pcl\\Zepp20220510114943_GPS strange.pcl']
194.0 146.0
0:00:00.405 ₀╷₀₀╷₀₀.₄₀₅ data\pcl\Zepp20220510114943_GPS strange.pcl
